Instalação do Java JDK 8

In [19]:
!sudo apt-get update
!sudo apt-get install -y openjdk-8-jdk openssh-server
!sudo update-alternatives --config java <<< '2'

Hit:1 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease
Hit:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Hit:3 http://security.ubuntu.com/ubuntu jammy-security InRelease
Hit:4 http://archive.ubuntu.com/ubuntu jammy InRelease
Hit:5 http://archive.ubuntu.com/ubuntu jammy-updates InRelease
Hit:6 http://archive.ubuntu.com/ubuntu jammy-backports InRelease
Hit:7 https://ppa.launchpadcontent.net/c2d4u.team/c2d4u4.0+/ubuntu jammy InRelease
Hit:8 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:9 https://ppa.launchpadcontent.net/graphics-drivers/ppa/ubuntu jammy InRelease
Hit:10 https://ppa.launchpadcontent.net/ubuntugis/ppa/ubuntu jammy InRelease
Reading package lists... Done
Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
openssh-server is already the newest version (1:8.9p1-3ubuntu0.4).
openjdk-8-jdk is already the newest version (8u382-ga-1~22.04.1).
0 upg

In [20]:
!ssh-keygen -q -t rsa -N '' -P '' -f /root/.ssh/id_rsa <<<y >/dev/null 2>&1
!ls -lahtr /root/.ssh/*
!cat /root/.ssh/id_rsa.pub >> /root/.ssh/authorized_keys
!sudo /etc/init.d/ssh start

-rw-r--r-- 1 root root  284 Sep 19 14:17 /root/.ssh/known_hosts.old
-rw-r--r-- 1 root root  284 Sep 19 14:19 /root/.ssh/known_hosts
-rw-r--r-- 1 root root 2.3K Sep 19 14:24 /root/.ssh/authorized_keys
-rw-r--r-- 1 root root  571 Sep 19 14:29 /root/.ssh/id_rsa.pub
-rw------- 1 root root 2.6K Sep 19 14:29 /root/.ssh/id_rsa
 * Starting OpenBSD Secure Shell server sshd
   ...done.


Download do Apache Hadoop

In [21]:
!rm -rf /content/hadoop-3.3.6
!rm -rf /content/hadoop-3.3.6*
!wget https://dlcdn.apache.org/hadoop/common/hadoop-3.3.6/hadoop-3.3.6.tar.gz
!tar -zxvf hadoop-3.3.6.tar.gz
!mv hadoop-3.3.6 hadoop

A saída de streaming foi truncada nas últimas 5000 linhas.
hadoop-3.3.6/share/doc/hadoop/hadoop-project-dist/hadoop-hdfs-client/build/source/hadoop-hdfs-project/hadoop-hdfs-client/target/api/org/apache/hadoop/hdfs/web/resources/DeleteOpParam.Op.html
hadoop-3.3.6/share/doc/hadoop/hadoop-project-dist/hadoop-hdfs-client/build/source/hadoop-hdfs-project/hadoop-hdfs-client/target/api/org/apache/hadoop/hdfs/web/resources/PutOpParam.html
hadoop-3.3.6/share/doc/hadoop/hadoop-project-dist/hadoop-hdfs-client/build/source/hadoop-hdfs-project/hadoop-hdfs-client/target/api/org/apache/hadoop/hdfs/web/resources/RenameOptionSetParam.html
hadoop-3.3.6/share/doc/hadoop/hadoop-project-dist/hadoop-hdfs-client/build/source/hadoop-hdfs-project/hadoop-hdfs-client/target/api/org/apache/hadoop/hdfs/web/resources/XAttrEncodingParam.html
hadoop-3.3.6/share/doc/hadoop/hadoop-project-dist/hadoop-hdfs-client/build/source/hadoop-hdfs-project/hadoop-hdfs-client/target/api/org/apache/hadoop/hdfs/web/resources/GetOpPar

In [22]:
!export JAVA_HOME=/usr/lib/jvm/java-8-openjdk-amd64/jre
!export HADOOP_HOME=/content/hadoop
!export HADOOP_INSTALL=$HADOOP_HOME
!export HADOOP_MAPRED_HOME=$HADOOP_HOME
!export HADOOP_COMMON_HOME=$HADOOP_HOME
!export HADOOP_HDFS_HOME=$HADOOP_HOME
!export HADOOP_YARN_HOME=$HADOOP_HOME
!export HADOOP_COMMON_LIB_NATIVE_DIR=$HADOOP_HOME/lib/native
!export PATH=$PATH:$HADOOP_HOME/sbin:$HADOOP_HOME/bin

!echo "export JAVA_HOME=/usr/lib/jvm/java-8-openjdk-amd64/jre" >> /content/hadoop/etc/hadoop/hadoop-env.sh
!echo "export HADOOP_HOME=/content/hadoop" >> /content/hadoop/etc/hadoop/hadoop-env.sh
!echo "export HDFS_NAMENODE_USER=\"root\"" >> /content/hadoop/etc/hadoop/hadoop-env.sh
!echo "export HDFS_DATANODE_USER=\"root\"" >> /content/hadoop/etc/hadoop/hadoop-env.sh
!echo "export HDFS_SECONDARYNAMENODE_USER=\"root\"" >> /content/hadoop/etc/hadoop/hadoop-env.sh
!echo "export YARN_RESOURCEMANAGER_USER=\"root\"" >> /content/hadoop/etc/hadoop/hadoop-env.sh
!echo "export YARN_NODEMANAGER_USER=\"root\"" >> /content/hadoop/etc/hadoop/hadoop-env.sh

In [23]:
sh = """<?xml version="1.0" encoding="UTF-8"?>
<?xml-stylesheet type="text/xsl" href="configuration.xsl"?>
<configuration>
 <property>
 <name>fs.defaultFS</name>
 <value>hdfs://localhost:9001</value>
 </property>
</configuration>
"""
with open('/content/hadoop/etc/hadoop/core-site.xml', 'w') as file:
  file.write(sh)

In [24]:
sh = """<?xml version="1.0" encoding="UTF-8"?>
<?xml-stylesheet type="text/xsl" href="configuration.xsl"?>
<configuration>
 <property>
 <name>dfs.replication</name>
 <value>1</value>
 </property>
 <property>
 <name>dfs.name.dir</name>
 <value>file:///content/hadoop/hadoopdata/hdfs/namenode</value>
 </property>
 <property>
 <name>dfs.data.dir</name>
 <value>file:///content/hadoop/hadoopdata/hdfs/datanode</value>
 </property><property>
 <name>dfs.support.broken.append</name>
 <value>true</value>
 </property>
</configuration>
"""
with open('/content/hadoop/etc/hadoop/hdfs-site.xml', 'w') as file:
  file.write(sh)

!rm -rf /content/hadoop/hadoopdata
!mkdir -p /content/hadoop/hadoopdata/hdfs/{namenode,datanode}

In [25]:
sh = """<?xml version="1.0" encoding="UTF-8"?>
<?xml-stylesheet type="text/xsl" href="configuration.xsl"?>
<configuration>
 <property>
 <name>mapreduce.framework.name</name>
 <value>yarn</value>
 </property>
<property>
 <name>yarn.app.mapreduce.am.env</name>
 <value>HADOOP_MAPRED_HOME=/content/hadoop</value>
</property>
<property>
 <name>mapreduce.map.env</name>
 <value>HADOOP_MAPRED_HOME=/content/hadoop</value>
</property>
<property>
 <name>mapreduce.reduce.env</name>
 <value>HADOOP_MAPRED_HOME=/content/hadoop</value>
</property>
</configuration>
"""
with open('/content/hadoop/etc/hadoop/mapred-site.xml', 'w') as file:
  file.write(sh)

In [26]:
sh = """<?xml version="1.0" encoding="UTF-8"?>
<?xml-stylesheet type="text/xsl" href="configuration.xsl"?>
<configuration>
 <property>
 <name>yarn.nodemanager.aux-services</name>
 <value>mapreduce_shuffle</value>
 </property>
</configuration>
"""
with open('/content/hadoop/etc/hadoop/yarn-site.xml', 'w') as file:
  file.write(sh)

In [27]:
!/content/hadoop/bin/hdfs namenode -format

2023-09-19 14:30:32,359 INFO namenode.NameNode: STARTUP_MSG: 
/************************************************************
STARTUP_MSG: Starting NameNode
STARTUP_MSG:   host = cf651b6887fd/172.28.0.12
STARTUP_MSG:   args = [-format]
STARTUP_MSG:   version = 3.3.6
STARTUP_MSG:   classpath = /content/hadoop/etc/hadoop:/content/hadoop/share/hadoop/common/lib/jsch-0.1.55.jar:/content/hadoop/share/hadoop/common/lib/commons-codec-1.15.jar:/content/hadoop/share/hadoop/common/lib/woodstox-core-5.4.0.jar:/content/hadoop/share/hadoop/common/lib/jetty-http-9.4.51.v20230217.jar:/content/hadoop/share/hadoop/common/lib/kerb-simplekdc-1.0.1.jar:/content/hadoop/share/hadoop/common/lib/zookeeper-3.6.3.jar:/content/hadoop/share/hadoop/common/lib/jsr311-api-1.1.1.jar:/content/hadoop/share/hadoop/common/lib/netty-codec-4.1.89.Final.jar:/content/hadoop/share/hadoop/common/lib/netty-codec-dns-4.1.89.Final.jar:/content/hadoop/share/hadoop/common/lib/jcip-annotations-1.0-1.jar:/content/hadoop/share/hadoop/co

In [28]:
!export HDFS_NAMENODE_USER="root"
!export HDFS_DATANODE_USER="root"
!export HDFS_SECONDARYNAMENODE_USER="root"
!export YARN_RESOURCEMANAGER_USER="root"
!export YARN_NODEMANAGER_USER="root"

In [29]:
!/content/hadoop/sbin/stop-dfs.sh
!/content/hadoop/sbin/start-dfs.sh
!/content/hadoop/sbin/stop-yarn.sh
!/content/hadoop/sbin/start-yarn.sh

Stopping namenodes on [localhost]
Stopping datanodes
Stopping secondary namenodes [cf651b6887fd]
Starting namenodes on [localhost]
Starting datanodes
Starting secondary namenodes [cf651b6887fd]
Stopping nodemanagers
Stopping resourcemanager
Starting resourcemanager
Starting nodemanagers


In [30]:
!/content/hadoop/bin/hdfs dfs -mkdir /teste

In [32]:
!/content/hadoop/bin/hdfs dfs -ls /

Found 1 items
drwxr-xr-x   - root supergroup          0 2023-09-19 14:31 /teste


In [34]:
!/content/hadoop/bin/hdfs dfs -put /content/sample_data/california_housing_train.csv /teste
!/content/hadoop/bin/hdfs dfs -ls /teste
!/content/hadoop/bin/hdfs dfs -cat /teste/california_housing_train.csv

A saída de streaming foi truncada nas últimas 5000 linhas.
-121.390000,38.550000,25.000000,2171.000000,431.000000,1053.000000,422.000000,3.527800,126200.000000
-121.390000,38.550000,18.000000,1734.000000,467.000000,783.000000,447.000000,1.904400,154300.000000
-121.390000,38.510000,19.000000,1808.000000,375.000000,758.000000,320.000000,2.006200,92000.000000
-121.390000,38.430000,3.000000,2696.000000,384.000000,990.000000,316.000000,5.444500,237600.000000
-121.390000,36.160000,28.000000,1057.000000,249.000000,288.000000,130.000000,3.052600,146900.000000
-121.400000,39.330000,15.000000,2655.000000,493.000000,1200.000000,432.000000,3.517900,107200.000000
-121.400000,38.710000,15.000000,4680.000000,758.000000,2626.000000,729.000000,3.835500,107000.000000
-121.400000,38.630000,31.000000,1540.000000,452.000000,1079.000000,444.000000,1.857100,98700.000000
-121.400000,38.630000,30.000000,3626.000000,834.000000,1577.000000,806.000000,2.517000,130400.000000
-121.400000,38.620000,28.000000,3671.00

In [35]:
!/content/hadoop/bin/hdfs dfs -get /teste/california_housing_train.csv /tmp
!cat /tmp/california_housing_train.csv

A saída de streaming foi truncada nas últimas 5000 linhas.
-121.390000,38.550000,25.000000,2171.000000,431.000000,1053.000000,422.000000,3.527800,126200.000000
-121.390000,38.550000,18.000000,1734.000000,467.000000,783.000000,447.000000,1.904400,154300.000000
-121.390000,38.510000,19.000000,1808.000000,375.000000,758.000000,320.000000,2.006200,92000.000000
-121.390000,38.430000,3.000000,2696.000000,384.000000,990.000000,316.000000,5.444500,237600.000000
-121.390000,36.160000,28.000000,1057.000000,249.000000,288.000000,130.000000,3.052600,146900.000000
-121.400000,39.330000,15.000000,2655.000000,493.000000,1200.000000,432.000000,3.517900,107200.000000
-121.400000,38.710000,15.000000,4680.000000,758.000000,2626.000000,729.000000,3.835500,107000.000000
-121.400000,38.630000,31.000000,1540.000000,452.000000,1079.000000,444.000000,1.857100,98700.000000
-121.400000,38.630000,30.000000,3626.000000,834.000000,1577.000000,806.000000,2.517000,130400.000000
-121.400000,38.620000,28.000000,3671.00

In [59]:
!mkdir /content/gutenberg
!wget https://www.gutenberg.org/cache/epub/feeds/pg_catalog.csv
!rm -f /content/gutenberg/pg_catalog.csv
!mv pg_catalog.csv /content/gutenberg/pg_catalog.csv

mkdir: cannot create directory ‘/content/gutenberg’: File exists
--2023-09-19 14:59:36--  https://www.gutenberg.org/cache/epub/feeds/pg_catalog.csv
Resolving www.gutenberg.org (www.gutenberg.org)... 152.19.134.47, 2610:28:3090:3000:0:bad:cafe:47
Connecting to www.gutenberg.org (www.gutenberg.org)|152.19.134.47|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 14527919 (14M) [text/csv]
Saving to: ‘pg_catalog.csv’

pg_catalog.csv      100%[===================>]  13.85M  81.3MB/s    in 0.2s    

2023-09-19 14:59:37 (81.3 MB/s) - ‘pg_catalog.csv’ saved [14527919/14527919]



In [60]:
!/content/hadoop/bin/hdfs dfs -rm /gutenberg/pg_catalog.csv
!/content/hadoop/bin/hdfs dfs -rmdir /gutenberg
!/content/hadoop/bin/hdfs dfs -mkdir /gutenberg
!/content/hadoop/bin/hdfs dfs -put /content/gutenberg/pg_catalog.csv /gutenberg/pg_catalog.csv
!/content/hadoop/bin/hdfs dfs -ls /gutenberg
!/content/hadoop/bin/hdfs dfs -cat /gutenberg/pg_catalog.csv

A saída de streaming foi truncada nas últimas 5000 linhas.
6204,Text,2004-08-01,When Valmond Came to Pontiac: The Story of a Lost Napoleon. Volume 3.,en,"Parker, Gilbert, 1862-1932",Canadian fiction,PS,
6205,Text,2004-11-16,When Valmond Came to Pontiac: The Story of a Lost Napoleon. Complete,en,"Parker, Gilbert, 1862-1932",Canadian fiction,PS,
6206,Text,2004-08-01,"The Trail of the Sword, Volume 1",en,"Parker, Gilbert, 1862-1932",Canada -- History -- To 1763 (New France) -- Fiction,PS,
6207,Text,2004-08-01,"The Trail of the Sword, Volume 2",en,"Parker, Gilbert, 1862-1932",Canada -- History -- To 1763 (New France) -- Fiction,PS,
6208,Text,2004-08-01,"The Trail of the Sword, Volume 3",en,"Parker, Gilbert, 1862-1932",Canada -- History -- To 1763 (New France) -- Fiction,PS,
6209,Text,2004-08-01,"The Trail of the Sword, Volume 4",en,"Parker, Gilbert, 1862-1932",Canada -- History -- To 1763 (New France) -- Fiction,PS,
6210,Text,2004-11-16,"The Trail of the Sword, Complete",en,"Parker, Gilber

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



arden), 1876-","Philippines -- Description and travel; Educational assistance, American -- Philippines",DS,
20997,Text,2007-04-06,The Nürnberg Stove,en,"Ouida, 1839-1908; Kirk, Maria Louise, 1860-1938 [Illustrator]",Stoves -- Juvenile fiction; Austria -- Juvenile fiction,PZ,Children's Literature
20998,Text,2007-04-06,"A fundação da monarchia portugueza
narração anti-iberica",pt,"Vasconcelos, António Augusto Teixeira de, 1816-1878",Portugal -- History -- To 1385,DP,PT História
20999,Text,2007-04-06,"Á hora do crime
phantasia dramatica em 1 acto a proposito do assassinato do General Prim",pt,"Miranda, Francisco Luís Coutinho de, -1883",Drama,PQ,PT Teatro
21000,Text,2007-04-06,Faust: Eine Tragödie [erster Teil],de,"Goethe, Johann Wolfgang von, 1749-1832","German poetry; Legends -- Germany -- Drama; Faust, -approximately 1540 -- Drama; Magicians -- Drama",PT,Best Books Ever Listings; Banned Books from Anne Haight's list; DE Drama
21001,Text,2007-04-06,Terre-Neuve et les Terre-Neuviennes,fr

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



A saída de streaming foi truncada nas últimas 5000 linhas.
40900,Text,2012-09-30,A Literary and Historical Atlas of Asia,en,"Bartholomew, J. G. (John George), 1860-1920",Coinage -- Asia -- History; Asia -- Maps; Asia -- Historical geography -- Maps,DS,
40901,Text,2012-09-30,"The Gentleman and Lady's Book of Politeness and Propriety of Deportment, Dedicated to the Youth of Both Sexes",en,"Celnart, Elisabeth, 1796-1865",Etiquette,BJ,
40902,Text,2012-09-30,"Histoire amoureuse des Gaules; suivie des Romans historico-satiriques du XVIIe siècle, Tome IV",fr,"Bussy, Roger de Rabutin, comte de, 1618-1693; Livet, Charles-Louis, 1828-1897 [Contributor]; Boiteau d'Ambly, Paul, 1830-1886 [Editor]",France -- Court and courtiers; Erotic literature,DC; PQ,FR Séduction et libertinage
40903,Text,2012-09-30,"Motor Boat Boys on the Great Lakes; or, Exploring the Mystic Isle of Mackinac",en,"Arundel, Louis",Motorboats -- Juvenile fiction; Great Lakes Region (North America) -- Juvenile fiction,PZ,
40904,Te

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



A saída de streaming foi truncada nas últimas 5000 linhas.
58757,Text,2019-01-23,Chats on Old Silver,en,"Hayden, Arthur, 1868-1946",Silverwork -- Great Britain,NK,
58758,Text,2019-01-23,First Stage: Moon,en,"Hetschel, Dick",Science fiction; Short stories; Space flight to the moon -- Fiction; Astronauts -- Fiction,PS,
58759,Text,2019-01-23,"The British Journal of Dermatology, April 1905",en,"Various; MacLeod, J. M. H. (John MacLeod Hendrie), 1870-1954 [Editor]",Dermatology -- Periodicals; Skin -- Diseases -- Periodicals; Syphilis -- Periodicals,RL,
58760,Text,2019-01-23,Hirsipuumies: Sydäntalven tarina,fi,"Schildt, Runar, 1888-1925; Ahma, Ilmari, 1884-1933 [Translator]",Swedish drama -- Translations into Finnish,PT,
58761,Text,2019-01-23,"The Precious Name, Proofs of the Godhead, and a Hymn",en,"Church, J. (John), 1780?-1825?","Jesus Christ; Holy Spirit; Hymns, English",BT,
58762,Text,2019-01-24,The New-Year's Bargain,en,"Coolidge, Susan, 1835-1905; Ledyard, Addie [Illustrator]",Childre

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



537,Text,2022-07-16,Egy régi udvarház utolsó gazdája; Nők a tükör előtt; A vén szinész,hu,"Gyulai, Pál, 1826-1909; Schöpflin, Aladár, 1872-1950 [Contributor]; Bér, Dezső, 1875-1924 [Illustrator]",Hungarian fiction -- 19th century,PH,
68538,Text,2022-07-16,"The skeleton scout; or, The border block",en,"Aiken, Albert W., 1846-1894","Indians of North America -- Fiction; Soldiers -- Fiction; Ghost stories; Dime novels; Wyandot Indians -- Fiction; Apparitions -- Fiction; Scouts (Reconnaissance) -- Fiction; Tecumseh, Shawnee chief, 1768-1813 -- Fiction; Tenskwatawa, Shawnee Prophet -- Fiction; Potawatomi Indians -- Fiction",PS,
68539,Text,2022-07-17,The Shakespeare garden club: A fantasy,en,"Moran, Mabel M.","Shakespeare, William, 1564-1616 -- Drama; Dramatists -- Drama",PR,
68540,Text,2022-07-17,Pelts and palisades: The story of fur and the rivalry for pelts in early America,en,"Hale, Nathaniel C. (Nathaniel Claiborne), 1903-1948; Jones, Elmo, -1971 [Illustrator]","United States -- History 

In [61]:
!/content/hadoop/bin/hdfs dfs -rm  /gutenberg-output/*
!/content/hadoop/bin/hdfs dfs -rmdir /gutenberg-output
!/content/hadoop/bin/hadoop jar /content/hadoop/share/hadoop/mapreduce/hadoop-mapreduce-examples-3.3.6.jar wordcount /gutenberg/pg_catalog.csv /gutenberg-output/

Deleted /gutenberg-output/_SUCCESS
Deleted /gutenberg-output/part-r-00000
2023-09-19 15:00:30,129 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at /0.0.0.0:8032
2023-09-19 15:00:30,809 INFO mapreduce.JobResourceUploader: Disabling Erasure Coding for path: /tmp/hadoop-yarn/staging/root/.staging/job_1695133888069_0004
2023-09-19 15:00:31,310 INFO input.FileInputFormat: Total input files to process : 1
2023-09-19 15:00:31,848 INFO mapreduce.JobSubmitter: number of splits:1
2023-09-19 15:00:32,107 INFO mapreduce.JobSubmitter: Submitting tokens for job: job_1695133888069_0004
2023-09-19 15:00:32,107 INFO mapreduce.JobSubmitter: Executing with tokens: []
2023-09-19 15:00:32,476 INFO conf.Configuration: resource-types.xml not found
2023-09-19 15:00:32,477 INFO resource.ResourceUtils: Unable to find 'resource-types.xml'.
2023-09-19 15:00:32,623 INFO impl.YarnClientImpl: Submitted application application_1695133888069_0004
2023-09-19 15:00:32,694 INFO mapreduce.J

In [70]:
!/content/hadoop/bin/hdfs dfs -ls /gutenberg-output/
!/content/hadoop/bin/hdfs dfs -cat /gutenberg-output/part-r-00000

A saída de streaming foi truncada nas últimas 5000 linhas.
47257,Text,2014-11-01,Prinssi	1
47258,Text,2014-11-01,American	1
47259,Text,2014-11-01,"La	1
4726,Text,2003-12-01,John	1
47260,Text,2014-11-01,"Reise	1
47261,Text,2014-11-01,"The	1
47262,Text,2014-11-01,"Old	1
47263,Text,2014-11-01,The	1
47264,Text,2014-11-02,The	1
47265,Text,2014-01-01,Pixies'	1
47266,Text,2014-11-02,Four	1
47267,Text,2014-11-02,C.	1
47268,Text,2014-11-02,Alte	1
47269,Text,2014-11-07,"Over	1
4727,Text,2003-12-01,John	1
47270,Text,2014-11-02,Rathfelder's	1
47271,Text,2014-11-02,The	1
47272,Text,2014-11-02,The	1
47273,Text,2014-11-03,"The	1
47274,Text,2014-11-03,"History	1
47275,Text,2014-11-03,Kotiopettajattaren	1
47276,Text,2014-11-03,"Gli	1
47277,Text,2014-11-03,"Gli	1
47278,Text,2014-11-03,"Gli	1
47279,Text,2014-11-03,The	1
4728,Text,2004-09-29,"John	1
47280,Text,2014-11-04,"Birds	1
47281,Text,2014-11-04,"The	1
47282,Text,2014-11-04,A	1
47283,Text,2014-11-04,"Lazy	1
47284,Text,2014-11-04,Favorite	1
47285,Tex

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [67]:
!wget -O const.pdf https://www2.camara.leg.br/atividade-legislativa/legislacao/constituicao1988/arquivos/ConstituicaoTextoAtualizado_EC%20127_128.pdf
!pip install PyPDF2

--2023-09-19 15:10:58--  https://www2.camara.leg.br/atividade-legislativa/legislacao/constituicao1988/arquivos/ConstituicaoTextoAtualizado_EC%20127_128.pdf
Resolving www2.camara.leg.br (www2.camara.leg.br)... 200.219.133.106
Connecting to www2.camara.leg.br (www2.camara.leg.br)|200.219.133.106|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 917700 (896K) [application/pdf]
Saving to: ‘const.pdf’

const.pdf           100%[===================>] 896.19K  1.31MB/s    in 0.7s    

2023-09-19 15:11:00 (1.31 MB/s) - ‘const.pdf’ saved [917700/917700]



In [68]:
from PyPDF2 import PdfReader

reader = PdfReader('const.pdf')
number_of_pages = len(reader.pages)
page = reader.pages[0]
text = page.extract_text()

with open(r"const.txt","a") as file:
  file.writelines(text)

In [69]:
!/content/hadoop/bin/hdfs dfs -rm /contituicao/const.txt
!/content/hadoop/bin/hdfs dfs -rmdir /contituicao
!/content/hadoop/bin/hdfs dfs -mkdir /contituicao
!/content/hadoop/bin/hdfs dfs -put /content/const.txt /contituicao/const.txt
!/content/hadoop/bin/hdfs dfs -ls /contituicao
!/content/hadoop/bin/hdfs dfs -cat /contituicao/const.txt

rm: `/contituicao/const.txt': No such file or directory
Found 1 items
-rw-r--r--   1 root supergroup       2086 2023-09-19 15:11 /contituicao/const.txt
 
 
 
 
 
CÂMARA DOS DEPUTADOS 
Centro de Documentação e Informação 
 
CONSTITUIÇÃO DA REPÚBLICA FEDERATIVA DO BRASIL 
 
PREÂMBULO 
 
 
Nós, representantes do povo brasileiro, reunidos em  Assembléia Nacional 
Constituinte para instituir um Estado democrático, destinado a assegurar o exercício dos 
direitos sociais e individuais, a liberdade, a segu rança, o bem-estar, o desenvolvimento, a 
igualdade e a justiça como valores supremos de uma sociedade fraterna, pluralista e sem 
preconceitos, fundada na harmonia social e comprome tida, na ordem interna e internacional, 
com a solução pacífica das controvérsias, promulgam os, sob a proteção de Deus, a seguinte 
Constituição da República Federativa do Brasil.  
 
TÍTULO I  
DOS PRINCÍPIOS FUNDAMENTAIS  
 
Art. 1º  A República Federativa do Brasil, formada pela uniã o indissolúvel dos 
Esta

In [80]:
!/content/hadoop/bin/hdfs dfs -rm  /contituicao-output/*
!/content/hadoop/bin/hdfs dfs -rmdir /contituicao-output
!/content/hadoop/bin/hadoop jar /content/hadoop/share/hadoop/mapreduce/hadoop-mapreduce-examples-3.3.6.jar wordcount /contituicao/const.txt /contituicao-output/

Deleted /contituicao-output/_SUCCESS
Deleted /contituicao-output/part-r-00000
2023-09-19 15:30:10,839 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at /0.0.0.0:8032
2023-09-19 15:30:11,576 INFO mapreduce.JobResourceUploader: Disabling Erasure Coding for path: /tmp/hadoop-yarn/staging/root/.staging/job_1695133888069_0007
2023-09-19 15:30:12,076 INFO input.FileInputFormat: Total input files to process : 1
2023-09-19 15:30:12,599 INFO mapreduce.JobSubmitter: number of splits:1
2023-09-19 15:30:13,268 INFO mapreduce.JobSubmitter: Submitting tokens for job: job_1695133888069_0007
2023-09-19 15:30:13,269 INFO mapreduce.JobSubmitter: Executing with tokens: []
2023-09-19 15:30:13,633 INFO conf.Configuration: resource-types.xml not found
2023-09-19 15:30:13,633 INFO resource.ResourceUtils: Unable to find 'resource-types.xml'.
2023-09-19 15:30:13,741 INFO impl.YarnClientImpl: Submitted application application_1695133888069_0007
2023-09-19 15:30:13,807 INFO mapredu

In [72]:
!/content/hadoop/bin/hdfs dfs -ls /contituicao-output/
!/content/hadoop/bin/hdfs dfs -cat /contituicao-output/part-r-00000

Found 2 items
-rw-r--r--   1 root supergroup          0 2023-09-19 15:13 /contituicao-output/_SUCCESS
-rw-r--r--   1 root supergroup       2042 2023-09-19 15:13 /contituicao-output/part-r-00000
-	12
.	1
1º	1
2º	1
3º	1
4º	1
A	2
Art.	4
Assembléia	1
BRASIL	1
Brasil	1
Brasil,	1
Brasil.	1
Brasil:	1
CONSTITUIÇÃO	1
Centro	1
Constituem	1
Constituinte	1
Constituição	1
Constituição.	1
CÂMARA	1
DA	1
DEPUTADOS	1
DO	1
DOS	2
Deus,	1
Distrito	1
Documentação	1
Estado	2
Estados	1
Executivo	1
FEDERATIVA	1
FUNDAMENTAIS	1
Fede	1
Federal,	1
Federativa	3
I	4
II	3
III	3
IV	2
Informação	1
Judiciário.	1
Legislativo,	1
Municípios	1
Nacional	1
Nós,	1
PREÂMBULO	1
PRINCÍPIOS	1
Parágrafo	1
Poderes	1
REPÚBLICA	1
República	4
São	1
Todo	1
TÍTULO	1
União,	1
V	1
a	13
a;	1
as	1
assegurar	1
autodeterminação	1
bem	1
bem-estar,	1
brasileiro,	1
cidadania;	1
com	1
como	2
comprome	1
constit	1
construir	1
controvérsias,	1
cor,	1
d	2
da	5
das	1
de	7
democrático	1
democrático,	1
desenvolvimento	1
desenvolvimento,	1
desigualdades	

In [83]:
sh = """import sys

for line in sys.stdin:
    line = line.strip()
    words = line.split()

    for word in words:
        print('%s\t%s' % (word,1))

"""
with open('/content/mapper.py', 'w') as file:
  file.write(sh)

In [84]:
sh = """import sys
from operator import itemgetter

current_word = None
current_count = 0
word = None

for line in sys.stdin:
    line = line.strip()
    word, count = line.split('\t',1)

    try:
        count = int(count)
    except ValueError:
        continue

    if current_word == word:
        current_count += count
    else:
        if current_word:
            print('%s\t%s'%(current_word, current_count))

        current_count = count
        current_word = word

if current_word == word:
    print('%s\t%s'%(current_word, current_count))

"""
with open('/content/reducer.py', 'w') as file:
  file.write(sh)

In [85]:
!/content/hadoop/bin/hdfs dfs -rm  /contituicao-output-py/*
!/content/hadoop/bin/hdfs dfs -rmdir /contituicao-output-py
!/content/hadoop/bin/hadoop jar /content/hadoop/share/hadoop/tools/lib/hadoop-streaming-3.3.6.jar \
-D mapreduce.job.framework.name=yarn \
-D mapreduce.job.reduces=1 \
-files mapper.py,reducer.py \
-mapper "python mapper.py" \
-reducer "python reducer.py" \
-input /contituicao/const.txt \
-output /contituicao-output-py$(date +"%Y_%m_%d_%H_%M_%S")

rm: `/contituicao-output-py/*': No such file or directory
rmdir: `/contituicao-output-py': No such file or directory
packageJobJar: [/tmp/hadoop-unjar2295460711894077623/] [] /tmp/streamjob54212887715708392.jar tmpDir=null
2023-09-19 16:25:10,151 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at /0.0.0.0:8032
2023-09-19 16:25:10,469 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at /0.0.0.0:8032
2023-09-19 16:25:10,874 INFO mapreduce.JobResourceUploader: Disabling Erasure Coding for path: /tmp/hadoop-yarn/staging/root/.staging/job_1695133888069_0010
2023-09-19 16:25:11,549 INFO mapred.FileInputFormat: Total input files to process : 1
2023-09-19 16:25:11,662 INFO mapreduce.JobSubmitter: number of splits:2
2023-09-19 16:25:12,332 INFO mapreduce.JobSubmitter: Submitting tokens for job: job_1695133888069_0010
2023-09-19 16:25:12,333 INFO mapreduce.JobSubmitter: Executing with tokens: []
2023-09-19 16:25:12,683 INFO conf.Configur

In [86]:
!/content/hadoop/bin/hdfs dfs -ls /contituicao-output-py2023_09_19_16_25_05/
!/content/hadoop/bin/hdfs dfs -cat /contituicao-output-py2023_09_19_16_25_05/part-r-00000

Found 2 items
-rw-r--r--   1 root supergroup          0 2023-09-19 16:25 /contituicao-output-py2023_09_19_16_25_05/_SUCCESS
-rw-r--r--   1 root supergroup       2042 2023-09-19 16:25 /contituicao-output-py2023_09_19_16_25_05/part-00000
cat: `/contituicao-output-py2023_09_19_16_25_05/part-r-00000': No such file or directory
